In [1]:
import pymysql
import json
import matplotlib.pyplot as plt
from functools import partial
import csv
import networkx as nx
import freeman as fm
from random import random, choices
def run_db_query(connection, query, args=None):
    with connection.cursor() as cursor:
        print('Executando query:')
        cursor.execute(query, args)
        for result in cursor:
            print(result)
            
def return_db_results(connection, query, args=None):#Gambiarra para pegar o id
    with connection.cursor() as cursor:
        cursor.execute(query, args)
        for result in cursor:
            return result #retorna logo o primeiro

def multiple_db_results(connection, query, args=None):#Gambiarra para pegar o id
    with connection.cursor() as cursor:
        cursor.execute(query, args)
        res = cursor.fetchall()
        return res

connection = pymysql.connect(
    host='localhost',
    user='root',
    password='vlm1998',
    database='redes')

db = partial(run_db_query, connection)

In [2]:
def add_node(g, n):
    try:
        g.add_node(n)
        g.nodes[n]['pos'] = (random(), random())
        g.nodes[n]['label'] = n
        g.nodes[n]['color'] = (255, 0, 0)
    except Exception as e:
        print(e)

def add_edge(g, n, m, peso):
    #print("De: ", n, "para: ", m, "peso: ", peso)
    g.add_edge(n, m)
    g[n][m]['weight'] = peso

def get_team_name(connection, id_team):
    with connection.cursor() as cursor:
        cursor.execute("SELECT nome FROM times WHERE id_time = %s", (id_team))
        res = cursor.fetchone()
        if res:
            return res
        else:
            return -1
def get_team_id(connection, nome):
    with connection.cursor() as cursor:
        cursor.execute("SELECT id_time FROM times WHERE nome=%s", (nome))
        res = cursor.fetchone()
        if res:
            return res
        else:
            return -1
def list_all_teams(connection):
    with connection.cursor() as cursor:
        cursor.execute("SELECT nome FROM times")
        res = cursor.fetchall()
        return res
def list_all_transfers(connection, ano):
    with connection.cursor() as cursor:
        cursor.execute("SELECT * FROM transferencia WHERE ano=%s", (ano))
        res = cursor.fetchall()
        return res
def get_from_where(connection, id_jogador, ano):
    #print(ano-1)
    with connection.cursor() as cursor:
        cursor.execute("SELECT times.nome FROM waived INNER JOIN times USING(id_time) WHERE id_jogador = %s AND ano = %s ", (id_jogador, ano))
        res = cursor.fetchone()
        if res:
            return res
        else:
            #buscar no ano anterior
            cursor.execute("SELECT times.nome FROM waived INNER JOIN times USING(id_time) WHERE id_jogador = %s AND ano = %s ", (id_jogador, ano-1))
            res = cursor.fetchone()
            if(res):
                #print("achou em 2018")
                return res
            else:
                #print(id_jogador, ano)
                return (-1,)
def get_weight(connection, id_time1, id_time2, ano):
    with connection.cursor() as cursor:
        cursor.execute("SELECT peso FROM rivalidade WHERE id_time1=%s AND id_time2=%s AND ano=%s", (id_time1, id_time2, ano))
        res = cursor.fetchone()
        if res:
            return res[0]
        else: #Pode ser que os nomes estejam invertidos nao sei
            cursor.execute("SELECT peso FROM rivalidade WHERE id_time1=%s AND id_time2=%s AND ano=%s", (id_time2, id_time1, ano))
            res = cursor.fetchone()
            if res:
                return res[0]
            return -1
def get_player_name(connection, id_jogador):
    with connection.cursor() as cursor:
        cursor.execute("SELECT nome FROM jogador WHERE id_jogador=%s", (id_jogador))
        res = cursor.fetchone()
        if(res):
            return res
        else:
            return -1

In [ ]:
a = fm.Animation()
g_2019 = nx.DiGraph()
a.rec(g_2019)

transfers = list_all_transfers(connection, 2019)
teams = list_all_teams(connection)

for team in teams:
    add_node(g_2019, team[0])
    
#Existem casos em que um time assina com um jogador e na mesma temporada vende ele, vamos ignorar estes casos por enquanto
for transfer in transfers:
    nome_jogador = get_player_name(connection, transfer[2])[0]
    antigo = get_from_where(connection, transfer[1], transfer[3])[0]
    novo = get_team_name(connection, transfer[2])[0]
    if(nome_jogador == 'Jimmy Butler'):
        print(antigo, novo)
    
    if(antigo != -1) and (novo != -1):
        if(antigo != novo):
            id_antigo = get_team_id(connection, antigo)
            id_novo = get_team_id(connection, novo)
            weight = get_weight(connection, id_antigo, id_novo, 2019)
            if(weight == -1):
                weight = 0
            add_edge(g_2019, antigo, novo, weight)
    else:
        continue
        #print(antigo, novo)
        #print(transfer[1])
    
a.rec(g_2019)
a.play()

In [ ]:


a = fm.Animation()
g_2018 = nx.DiGraph()
a.rec(g_2018)

transfers = list_all_transfers(connection, 2018)
teams = list_all_teams(connection)

for team in teams:
    add_node(g_2018, team[0])

    
#Existem casos em que um time assina com um jogador e na mesma temporada vende ele, vamos ignorar estes casos por enquanto
for transfer in transfers:
    antigo = get_from_where(connection, transfer[1], transfer[3])[0]
    novo = get_team_name(connection, transfer[2])[0]
    if(antigo != -1) and (novo != -1):
        if(antigo != novo):
            id_antigo = get_team_id(connection, antigo)
            id_novo = get_team_id(connection, novo)
            weight = get_weight(connection, id_antigo, id_novo, 2018)
            if(weight == -1):
                weight = 0
            add_edge(g_2018, antigo, novo, weight)
    else:
        continue
        #print(antigo, novo)
    
    
a.rec(g_2018)
a.play()


In [ ]:
a = fm.Animation()
g_2017 = nx.DiGraph()
a.rec(g_2017)

transfers = list_all_transfers(connection, 2017)
teams = list_all_teams(connection)

for team in teams:
    add_node(g_2017, team[0])

    
#Existem casos em que um time assina com um jogador e na mesma temporada vende ele, vamos ignorar estes casos por enquanto
for transfer in transfers:
    antigo = get_from_where(connection, transfer[1], transfer[3])[0]
    novo = get_team_name(connection, transfer[2])[0]
    if(antigo != -1) and (novo != -1):
        if(antigo != novo):
            id_antigo = get_team_id(connection, antigo)
            id_novo = get_team_id(connection, novo)
            weight = get_weight(connection, id_antigo, id_novo, 2018)
            if(weight == -1):
                weight = 0
            add_edge(g_2017, antigo, novo, weight)
    else:
        continue
        #print(antigo, novo)
    
    
a.rec(g_2017)
a.play()

In [ ]:
a = fm.Animation()
g_2016 = nx.DiGraph()
a.rec(g_2016)

transfers = list_all_transfers(connection, 2016)
teams = list_all_teams(connection)

for team in teams:
    add_node(g_2016, team[0])

    
#Existem casos em que um time assina com um jogador e na mesma temporada vende ele, vamos ignorar estes casos por enquanto
for transfer in transfers:
    antigo = get_from_where(connection, transfer[1], transfer[3])[0]
    novo = get_team_name(connection, transfer[2])[0]
    if(antigo != -1) and (novo != -1):
        if(antigo != novo):
            id_antigo = get_team_id(connection, antigo)
            id_novo = get_team_id(connection, novo)
            weight = get_weight(connection, id_antigo, id_novo, 2018)
            if(weight == -1):
                weight = 0
            add_edge(g_2016, antigo, novo, weight)
    else:
        continue
        #print(antigo, novo)
    
    
a.rec(g_2016)
a.play()

In [ ]:
for n, m in g_2019.edges:
    try:
        if(g_2019.edges[n,m]['weight'] > 0):
            print('1')
    except Exception as e:
        print(e)
        print(g_2019.edges[n,m]['weight'])

for n, m in g_2018.edges:
    try:
        if( g_2018.edges[n,m]['weight'] > 0 ):
            print('1')
    except Exception as e:
        print(e)
        print(g_2018.edges[n,m]['weight'])

for n, m in g_2017.edges:
    try:
        if( g_2017.edges[n,m]['weight'] > 0 ):
            print('1')
    except Exception as e:
        print(e)
        print(g_2017.edges[n,m]['weight'])

for n, m in g_2016.edges:
    try:
        if( g_2016.edges[n,m]['weight'] > 0 ):
            print('1')
    except Exception as e:
        print(e)
        print(g_2016.edges[n,m]['weight'])


In [49]:
import freeman as fm
teams = list_all_teams(connection)
def colorize_edges(g):
    for n, m in g.edges:
        weight = g.edges[n, m]['weight']
        g.edges[n, m]['color'] = (0, 0, int(255*weight))

g_triads = nx.Graph()
for team in teams:
    add_node(g_triads, team[0])
g_triads = fm.Graph(g_triads)

for a in g_triads.nodes:
    for b in g_triads.nodes:
        if(a == b):
            continue
        else:
            a_id = get_team_id(connection,a)[0]
            b_id = get_team_id(connection,b)[0]
            weight = get_weight(connection, a_id, b_id, 2019)
            if(weight == -1):
                weight = 0
            add_edge(g_triads, a, b, weight)

In [50]:
a = fm.Animation()
a.rec(g_triads)

dr = 0.25
counter_caso1 = 0
counter_caso2 = 0
counter_caso3 = 0
counter_caso35 = 0
counter_caso4 = 0
while(dr > 0.01):
    print(dr)
    for n,m,l in g_triads.triads():        
        nm_weight = g_triads.edges[n,m]['weight']
        nl_weight = g_triads.edges[n,l]['weight']
        ml_weight = g_triads.edges[m,l]['weight']

        #Caso1 - R R R - nao faz nada
        if(nm_weight >= 0.5) and (nl_weight >= 0.5) and (ml_weight >= 0.5):
            counter_caso1+=1
            continue
        
        #Caso2 - R R X - vira R R dr
        elif(nm_weight >= 0.5) and (nl_weight >= 0.5):
            #Adiciona dr
            ml_weight += dr
            g_triads.edges[m,l]['weight'] = ml_weight
            counter_caso2+=1
        elif(nm_weight >= 0.5) and (ml_weight >= 0.5):
            #Adiciona dr
            nl_weight += dr
            g_triads.edges[n,l]['weight'] = nl_weight
            counter_caso2+=1
        elif(nl_weight >= 0.5) and (ml_weight >= 0.5):
            #Adiciona dr
            nm_weight += dr
            g_triads.edges[n,m]['weight'] = nm_weight
            counter_caso2+=1
            
        #Caso3 - R dx X - vira R dx ddx
        elif((nl_weight >= 0.5) and (ml_weight >= dr)):
            #2 vezes dr porque é da iteração anterior
            #Adiciona ddr
            nm_weight += dr/2
            g_triads.edges[n,m]['weight'] = nm_weight
            counter_caso3+=1

        elif((nm_weight >= 0.5) and (ml_weight >= dr)):
            #Adiciona ddr
            nl_weight += dr/2
            g_triads.edges[n,l]['weight'] = nl_weight
            counter_caso3+=1

        elif((nl_weight >= 0.5) and (nm_weight >= dr)):
            #Adiciona ddr
            ml_weight += dr/2
            g_triads.edges[m,l]['weight'] = ml_weight
            counter_caso3+=1
            
        #Caso3.5 - R ddx X - vira R ddx dddx
        elif((nl_weight >= 0.5) and (nm_weight >= dr/2)):
            #2 vezes dr porque é da iteração anterior
            #Adiciona ddr
            nm_weight += dr/4
            g_triads.edges[n,m]['weight'] = nm_weight
            counter_caso35+=1

        elif((nm_weight >= 0.5) and (ml_weight >= dr/2)):
            #Adiciona ddr
            nl_weight += dr/4
            g_triads.edges[n,l]['weight'] = nl_weight
            counter_caso35+=1

        elif((nl_weight >= 0.5) and (nm_weight >= dr/2)):
            #Adiciona ddr
            ml_weight += dr/4
            g_triads.edges[m,l]['weight'] = ml_weight
            counter_caso35+=1
             
        #Caso4 - R X X - nao faz nada, quem sabe na proxima iteração
        else:  
            counter_caso4+=1
            continue
    dr = dr/2
    a.rec(g_triads)
    colorize_edges(g_triads)
    g_triads.move('step', iterations=10)

a.rec(g_triads)
print("Caso1: ", counter_caso1)
print("Caso2: ", counter_caso2)
print("Caso3: ", counter_caso3)
print("Caso3.5: ", counter_caso35)
print("Caso4: ", counter_caso4)

a.play()


0.25
0.125
0.0625
0.03125
0.015625
Caso1:  584
Caso2:  423
Caso3:  1053
Caso3.5:  87
Caso4:  18153


In [51]:


teams = list_all_teams(connection)
def colorize_edges(g):
    for n, m in g.edges:
        weight = g.edges[n, m]['weight']
        g.edges[n, m]['color'] = (0, 0, int(255*weight))

g_triads_2018 = nx.Graph()
for team in teams:
    add_node(g_triads_2018, team[0])
g_triads_2018 = fm.Graph(g_triads_2018)

for a in g_triads_2018.nodes:
    for b in g_triads_2018.nodes:
        if(a == b):
            continue
        else:
            a_id = get_team_id(connection,a)[0]
            b_id = get_team_id(connection,b)[0]
            weight = get_weight(connection, a_id, b_id, 2018)
            if(weight == -1):
                weight = 0
            add_edge(g_triads_2018, a, b, weight)

In [52]:
a = fm.Animation()
a.rec(g_triads_2018)

dr = 0.25
counter_caso1 = 0
counter_caso2 = 0
counter_caso3 = 0
counter_caso35 = 0
counter_caso4 = 0
while(dr > 0.01):
    print(dr)
    for n,m,l in g_triads_2018.triads():        
        nm_weight = g_triads_2018.edges[n,m]['weight']
        nl_weight = g_triads_2018.edges[n,l]['weight']
        ml_weight = g_triads_2018.edges[m,l]['weight']

        #Caso1 - R R R - nao faz nada
        if(nm_weight >= 0.5) and (nl_weight >= 0.5) and (ml_weight >= 0.5):
            counter_caso1+=1
            continue
        
        #Caso2 - R R X - vira R R dr
        elif(nm_weight >= 0.5) and (nl_weight >= 0.5):
            #Adiciona dr
            ml_weight += dr
            g_triads_2018.edges[m,l]['weight'] = ml_weight
            counter_caso2+=1
        elif(nm_weight >= 0.5) and (ml_weight >= 0.5):
            #Adiciona dr
            nl_weight += dr
            g_triads_2018.edges[n,l]['weight'] = nl_weight
            counter_caso2+=1
        elif(nl_weight >= 0.5) and (ml_weight >= 0.5):
            #Adiciona dr
            nm_weight += dr
            g_triads_2018.edges[n,m]['weight'] = nm_weight
            counter_caso2+=1
            
        #Caso3 - R dx X - vira R dx ddx
        elif((nl_weight >= 0.5) and (ml_weight >= dr)):
            #2 vezes dr porque é da iteração anterior
            #Adiciona ddr
            nm_weight += dr/2
            g_triads_2018.edges[n,m]['weight'] = nm_weight
            counter_caso3+=1

        elif((nm_weight >= 0.5) and (ml_weight >= dr)):
            #Adiciona ddr
            nl_weight += dr/2
            g_triads_2018.edges[n,l]['weight'] = nl_weight
            counter_caso3+=1

        elif((nl_weight >= 0.5) and (nm_weight >= dr)):
            #Adiciona ddr
            ml_weight += dr/2
            g_triads_2018.edges[m,l]['weight'] = ml_weight
            counter_caso3+=1
            
        #Caso3.5 - R ddx X - vira R ddx dddx
        elif((nl_weight >= 0.5) and (nm_weight >= dr/2)):
            #2 vezes dr porque é da iteração anterior
            #Adiciona ddr
            nm_weight += dr/4
            g_triads_2018.edges[n,m]['weight'] = nm_weight
            counter_caso35+=1

        elif((nm_weight >= 0.5) and (ml_weight >= dr/2)):
            #Adiciona ddr
            nl_weight += dr/4
            g_triads_2018.edges[n,l]['weight'] = nl_weight
            counter_caso35+=1

        elif((nl_weight >= 0.5) and (nm_weight >= dr/2)):
            #Adiciona ddr
            ml_weight += dr/4
            g_triads_2018.edges[m,l]['weight'] = ml_weight
            counter_caso35+=1
             
        #Caso4 - R X X - nao faz nada, quem sabe na proxima iteração
        else:  
            counter_caso4+=1
            continue
    dr = dr/2
    a.rec(g_triads_2018)
    colorize_edges(g_triads_2018)
    g_triads_2018.move('step', iterations=10)

a.rec(g_triads_2018)
print("Caso1: ", counter_caso1)
print("Caso2: ", counter_caso2)
print("Caso3: ", counter_caso3)
print("Caso3.5: ", counter_caso35)
print("Caso4: ", counter_caso4)

a.play()


0.25
0.125
0.0625
0.03125
0.015625
Caso1:  234
Caso2:  447
Caso3:  803
Caso3.5:  62
Caso4:  18754


In [86]:
import pandas as pd
dict_2019 = {}
for n,m in g_triads.edges:
    dict_2019[n,m] = g_triads.edges[n,m]['weight']
df_2019 = pd.DataFrame.from_dict(dict_2019, orient='index')

dict_antigos = {}
for n,m in g_triads_2018.edges:
    dict_antigos[n,m] = g_triads_2018.edges[n,m]['weight']
df_antigos = pd.DataFrame.from_dict(dict_antigos, orient='index')

In [112]:
df_2019.columns = [Rivalidade pós algoritmo']
df_2019.loc[df_2019['Rivalidade pós algoritmo'] != 0]

SyntaxError: invalid syntax (<ipython-input-112-4bbf658f2396>, line 1)

In [109]:
df_antigos.columns = ['Rivalidade pós algoritmo']
df_antigos.loc[df_antigos['Rivalidade pos algoritmo'] != 0]

Rivalidade pós algoritmo
(Boston Celtics, Chicago Bulls)                               0.343750
(Boston Celtics, Cleveland Cavaliers)                         0.171875
(Boston Celtics, Dallas Mavericks)                            0.320312
(Boston Celtics, Detroit Pistons)                             0.500000
(Boston Celtics, Golden State Warriors)                       0.078125
...                                                                ...
(Portland Trail Blazers, Utah Jazz)                           0.062500
(Portland Trail Blazers, Washington Wizards)                  0.031250
(San Antonio Spurs, Utah Jazz)                                0.500000
(San Antonio Spurs, Washington Wizards)                       0.304688
(Utah Jazz, Washington Wizards)                               0.234375

[154 rows x 1 columns]

In [104]:
dict_comp = {}
for n,m in g_triads.edges:
    n_id = get_team_id(connection,n)[0]
    m_id = get_team_id(connection,m)[0]
    l_pesos = []
    weight = get_weight(connection, n_id, m_id, 2019)
    if(weight == -1):
        weight = 0
    l_pesos.append(weight)
    l_pesos.append(dict_2019[n,m])
    dict_comp[n,m] = l_pesos
df_comp = pd.DataFrame.from_dict(dict_comp, orient='index')
df_comp.columns = ['Rivalidade antiga', 'Rivalidade pos algoritmo']
df_comp

Rivalidade antiga  \
(Atlanta Hawks, Boston Celtics)                        0.0   
(Atlanta Hawks, Brooklyn Nets)                         0.0   
(Atlanta Hawks, Charlotte Hornets)                     0.0   
(Atlanta Hawks, Chicago Bulls)                         0.0   
(Atlanta Hawks, Cleveland Cavaliers)                   0.0   
...                                                    ...   
(San Antonio Spurs, Utah Jazz)                         0.0   
(San Antonio Spurs, Washington Wizards)                0.0   
(Toronto Raptors, Utah Jazz)                           0.0   
(Toronto Raptors, Washington Wizards)                  0.0   
(Utah Jazz, Washington Wizards)                        0.0   

                                         Rivalidade pós algoritmo  
(Atlanta Hawks, Boston Celtics)                           0.00000  
(Atlanta Hawks, Brooklyn Nets)                            0.00000  
(Atlanta Hawks, Charlotte Hornets)                        0.00000  
(Atlanta Hawks, Chicago Bulls)                            0.00000  
(Atlanta Hawks, Cleveland Cavaliers)                      0.00000  
...                                                           ...  
(San Antonio Spurs, Utah Jazz)                            0.50000  
(San Antonio Spurs, Washington Wizards)                   0.50000  
(Toronto Raptors, Utah Jazz)                              0.00000  
(Toronto Raptors, Washington Wizards)                     0.00000  
(Utah Jazz, Washington Wizards)                           0.28125  

[435 rows x 2 columns]

In [105]:
dict_comp_antigos = {}
for n,m in g_triads_2018.edges:
    n_id = get_team_id(connection,n)[0]
    m_id = get_team_id(connection,m)[0]
    l_pesos = []
    weight = get_weight(connection, n_id, m_id, 2019)
    if(weight == -1):
        weight = 0
    l_pesos.append(weight)
    l_pesos.append(dict_antigos[n,m])
    dict_comp_antigos[n,m] = l_pesos
df_comp_antigos = pd.DataFrame.from_dict(dict_comp_antigos, orient='index')
df_comp_antigos.columns = ['Rivalidade antiga', 'Rivalidade pos algoritmo']
df_comp_antigos

Rivalidade antiga  \
(Atlanta Hawks, Boston Celtics)                        0.0   
(Atlanta Hawks, Brooklyn Nets)                         0.0   
(Atlanta Hawks, Charlotte Hornets)                     0.0   
(Atlanta Hawks, Chicago Bulls)                         0.0   
(Atlanta Hawks, Cleveland Cavaliers)                   0.0   
...                                                    ...   
(San Antonio Spurs, Utah Jazz)                         0.0   
(San Antonio Spurs, Washington Wizards)                0.0   
(Toronto Raptors, Utah Jazz)                           0.0   
(Toronto Raptors, Washington Wizards)                  0.0   
(Utah Jazz, Washington Wizards)                        0.0   

                                         Rivalidade pós algoritmo  
(Atlanta Hawks, Boston Celtics)                          0.000000  
(Atlanta Hawks, Brooklyn Nets)                           0.000000  
(Atlanta Hawks, Charlotte Hornets)                       0.000000  
(Atlanta Hawks, Chicago Bulls)                           0.000000  
(Atlanta Hawks, Cleveland Cavaliers)                     0.000000  
...                                                           ...  
(San Antonio Spurs, Utah Jazz)                           0.500000  
(San Antonio Spurs, Washington Wizards)                  0.304688  
(Toronto Raptors, Utah Jazz)                             0.000000  
(Toronto Raptors, Washington Wizards)                    0.000000  
(Utah Jazz, Washington Wizards)                          0.234375  

[435 rows x 2 columns]

In [121]:
export = df_2019.to_json ('./rivalidades2019.json', orient='split')
json.dump()

In [ ]:
connection.close()